<center><h1> GEARS Dataset </h1></center>

## Context

This notebook intend to load the dataset used in GEARS and in the benchmarking paper [\[1\]](#benchmark).

In particular, we will be using the following [datasets](#datasets).

## Table of Contents

- [Raw Data](#raw-pipeline)
- [Pre-processed Data](#pre-processed-pipeline)

## Datasets

### Raw Data

- [Adamson](https://www.ncbi.nlm.nih.gov/geo/query/acc.cgi?acc=GSE90546): 
  - ht<span>tps://</span>www.ncbi.nlm.nih.gov/geo/download/?acc=GSE90546&format=file
  - Assay type: perturb-seq: a combination of droplet based scRNAseq with a strategy for barcoding CRISPR-mediated perturbations.
  - Single CRIPSRi perturbation.
  - Overall: 3 different pooled CRIPSR screening experiments were conducted via perturb-seq.
- [Replogle](https://plus.figshare.com/articles/dataset/_Mapping_information-rich_genotype-phenotype_landscapes_with_genome-scale_Perturb-seq_Replogle_et_al_2022_processed_Perturb-seq_datasets/20029387):
  - Single cell raw **K562 genome scale scale day 8 post-transduction** ht<span>tps://</span>plus.figshare.com/ndownloader/files/35775507
  - Single cell raw **K562 essential scale day 6 post-transduction** ht<span>tps://</span>plus.figshare.com/ndownloader/files/35773219
  - Single cell raw **RPE1 essential scale  day 7 post-transduction** ht<span>tps://</span>plus.figshare.com/ndownloader/files/35775606
- [Norman](https://www.ncbi.nlm.nih.gov/geo/query/acc.cgi?acc=GSE133344):
  - raw_barcodes.tsv.gz: ht<span>tps://</span>ftp.ncbi.nlm.nih.gov/geo/series/GSE133nnn/GSE133344/suppl/GSE133344%5Fraw%5Fbarcodes.tsv.gz
  - raw_cell_identities.csv.gz: ht<span>tps://</span>ftp.ncbi.nlm.nih.gov/geo/series/GSE133nnn/GSE133344/suppl/GSE133344%5Fraw%5Fcell%5Fidentities.csv.gz
  - raw_genes.tsv.gz: ht<span>tps://</span>ftp.ncbi.nlm.nih.gov/geo/series/GSE133nnn/GSE133344/suppl/GSE133344%5Fraw%5Fgenes.tsv.gz
  - raw_matrix.mtx.gz: ht<span>tps://</span>ftp.ncbi.nlm.nih.gov/geo/series/GSE133nnn/GSE133344/suppl/GSE133344%5Fraw%5Fmatrix.mtx.gz

### Pre-processed Data
For completeness, here are the datasets used by GEARS or scFoundation and the benchmarking paper [\[1\]](#benchmark).

**GEARS**:

- Single-gene perturbation:
  - [Adamson](https://dataverse.harvard.edu/file.xhtml?fileId=6154417&version=3.0&toolType=PREVIEW): ht<span>tps://</span>dataverse.harvard.edu/api/access/datafile/6154417
  - [Relogle K562](https://dataverse.harvard.edu/file.xhtml?fileId=7458695&version=6.0&toolType=PREVIEW): ht<span>tps://</span>dataverse.harvard.edu/api/access/datafile/7458695
  - [Replogle RPE1](https://dataverse.harvard.edu/file.xhtml?fileId=7458694&version=6.0&toolType=PREVIEW): ht<span>tps://</span>dataverse.harvard.edu/api/access/datafile/7458694

- Multiple-gene perturbation
  - [Norman](https://dataverse.harvard.edu/file.xhtml?fileId=6154020&version=3.0&toolType=PREVIEW): ht<span>tps://</span>dataverse.harvard.edu/api/access/datafile/6154020
  - 131 two-gene perturbations

**scFoundation**:

Another preprocessing strategy for the Norman et al. dataset
- [Norman scFoundation](https://figshare.com/articles/dataset/scFoundation_Large_Scale_Foundation_Model_on_Single-cell_Transcriptomics_-_processed_datasets/24049200?file=44477939): ht<span>tps://</span>figshare.com/ndownloader/files/44477939
## References

1. Ahlmann-Eltze, Huber, and Anders, “Deep Learning-Based Predictions of Gene Perturbation Effects Do Not yet Outperform Simple Linear Baselines.”<a id="benchmark"></a>


## 1) Download Datasets

Note that the bash script is run from the Notebook but you can also run it from the shell. File will be downloaded using the `yaml` config in `fine tune/config/download.yaml`.

In [ ]:
%%bash
cd ../../ # cd to root of the project
python fine_tune/scripts/download/cli.py --config fine_tune/datasets/config/download.yaml

## 2) Create AnnData From Raw

In [1]:
# All imports here
from pathlib import Path

import anndata as ad
import pandas as pd
import pooch
import scanpy as sc

data_path = Path("./../datasets")


%reload_ext autoreload
%autoreload 2


### a) Adamson

**Note on Adamson**

| Accession              | Experiment                    | Model                               | Protocol                                                                                    | Additional Protocol                                                                                                                          | sgRNA Count                                                                               | Cell Count | Assay Type           |
| ---------------------- | ------------------------------ | ----------------------------------- | ------------------------------------------------------------------------------------------- | -------------------------------------------------------------------------------------------------------------------------------------------- | ----------------------------------------------------------------------------------------- | ---------- | -------------------- |
| **GSM2406675\_10X001** | **Pilot Experiment**           | K562 cells with dCas9-KRAB (cBA010) | Individual transduction → pooled after 3 days → selection + 5 days combined growth          | Growth in the presence of puromycin (3µg/mL)                                                                                                                                            | 8 distinct GBCs (1 control)                                                               | 5,768      | 10x 3' v1  |
| **GSM2406677\_10X005** | **UPR Epistasis Experiment**   | K562 cells with dCas9-KRAB (cBA010) | Individual transduction → pooled after 3 days → selection + 2 days combined growth          | To limit heterogenous effects of cell microenvironments caused by cell settling, the sorted cells were grown with continuous agitation on an orbital shaker. <br> <br> Pharmacological treatment: <br> • Thapsigargin (ER Ca²⁺ pump inhibitor) (100 nM/mL 100 nM for 4 hr.)<br> • Tunicamycin (N-glycosylation inhibitor) (4 μg/mL for 6h) <br> • DMSO (control) for 6hr | 7 GBCs (3-guide vectors of 3 genes — single, double, triple) + 2 triple negative controls | 15,006     | 10x 3' v1            |
| **GSM2406681\_10X010** | **UPR Perturb-seq Experiment** | K562 cells with dCas9-KRAB (cBA011) | Individual lentivirus production → pooled transduction → selection + 7 days combined growth | To limit heterogenous effects of cell microenvironments caused by cell settling, the sorted cells were grown with continuous agitation on an orbital shaker. <br><br> Sequencing across two separate runs totaling 10 lanes.                                                                                                                                            | 93 GBCs (2 control GBCs; targets cover 82 genes)                                          | 65,337     | 10x 3' v1 (10 lanes) |

**Remarque:**
- UPR (unfolded protein response)
- The assay technology is assumed to be the v1 of the Chromium Single Cell 3′ Solution (No specification of the version but 2016, launched year of the technology).
- When the identity of a Cas9 targeting single guide RNA (sgRNA) couldn't be uniquely identified, it was either:
  - "multiplet" 
  - "NaN"

In [2]:
adamson_dir = data_path.joinpath("raw/raw_adamson")
mtx_files = sorted(adamson_dir.glob("*_matrix.mtx.txt.gz"))

all_adatas = {}

for mtx_file in mtx_files:
    prefix = mtx_file.name.split("_matrix")[0]

    # Paths
    barcodes_file = adamson_dir / f"{prefix}_barcodes.tsv.gz"
    genes_file = adamson_dir / f"{prefix}_genes.tsv.gz"
    identities_file = adamson_dir / f"{prefix}_cell_identities.csv.gz"

    # Load metadata
    genes = pd.read_csv(genes_file, header=None, sep="\t")
    barcodes = pd.read_csv(barcodes_file, header=None)
    cell_identities = pd.read_csv(identities_file, index_col=0)

    # Create AnnData
    adata = ad.io.read_mtx(mtx_file).T
    adata.var_names = genes[0].values
    adata.obs_names = barcodes[0].values
    # adata.obs = cell_identities.loc[adata.obs_names] fail because more barcodes than cell_identity.
    adata.obs = pd.DataFrame(index=adata.obs_names)
    adata.obs = adata.obs.join(cell_identities) # fill with NaN barcodes with non found identity

    # Optional: keep track of the experiment
    adata.obs["experiment"] = prefix
    all_adatas[prefix] = adata

all_adatas

{'GSM2406675_10X001': AnnData object with n_obs × n_vars = 5768 × 35635
     obs: 'guide identity', 'read count', 'UMI count', 'coverage', 'good coverage', 'number of cells', 'experiment',
 'GSM2406677_10X005': AnnData object with n_obs × n_vars = 15006 × 32738
     obs: 'guide identity', 'read count', 'UMI count', 'coverage', 'good coverage', 'number of cells', 'experiment',
 'GSM2406681_10X010': AnnData object with n_obs × n_vars = 65337 × 32738
     obs: 'guide identity', 'read count', 'UMI count', 'coverage', 'good coverage', 'number of cells', 'experiment'}

#### i) Retrieve correct perturbation

Let's check the number of unique guide barcode which shall corresponds the unique perturbations (except than certain barcode targets the same genes).

In [3]:
print(
    "Number of unique 'guide barcode' detected:\n" +
    "\n".join([
        f"{exp}: {adata.obs['guide identity'].unique().__len__()}, "
        f"expected {gbc}, of which {control} controls "
        "+ eventually NaN or '*' for non identifiable and multiplets"
        for (exp, adata), (gbc, control) in zip(all_adatas.items(), zip([8, 9, 93],[1, 2, 2]))
    ])
)

Number of unique 'guide barcode' detected:
GSM2406675_10X001: 10, expected 8, of which 1 controls + eventually NaN or '*' for non identifiable and multiplets
GSM2406677_10X005: 21, expected 9, of which 2 controls + eventually NaN or '*' for non identifiable and multiplets
GSM2406681_10X010: 115, expected 93, of which 2 controls + eventually NaN or '*' for non identifiable and multiplets


**Filtering must occurs:**
- GSM2406675_10X001: 
  - Remove Nan and '*'
- GSM2406677_10X005: 
  - Remove Nan and '*'
  - Targeted genes should be a single, double or triple combination of:
    - ATF6
    - ERN1 (IRE1⍺)
    - EIF2AK3 (PERK) -> We must rename PERK in EIF2AK3 to match the actual gene name
- GSM2406681_10X010: 
  - Remove Nan and '*'
  - Shall use the "Table S1. Protospacer Sequences of sgRNAs"

In [4]:
adamson_pilot = all_adatas["GSM2406675_10X001"]
adamson_epistasis = all_adatas["GSM2406677_10X005"]
adamson_perturb = all_adatas["GSM2406681_10X010"]

In [5]:
# Pilot experiment - remove NaN and '*'
adamson_pilot = adamson_pilot[
    ~adamson_pilot.obs["guide identity"].astype(str).str.contains(r"(nan|\*)")
]
# UPR epistasis experiment - keep only guide containing any of ctrl, IRE1, PERK, ATF6
adamson_epistasis = adamson_epistasis[
    adamson_epistasis.obs["guide identity"].astype(str).str.contains("(ctrl|IRE1|PERK|ATF6)")
]

# UPR perturb seq experiment - retrieve table S1 and filter out guide while keeping control: 'mod'
file = pooch.retrieve(
    url="https://ars.els-cdn.com/content/image/1-s2.0-S0092867416316609-mmc1.xlsx",
    known_hash="sha256:9b5935cb15ba2f6d60d3017832de2918e7d4f172db6f202be7999cba5feea82b"
)
protospace_df = pd.read_excel(file, header=1)
# some gene are separated with '/'. Since the convention chosen is not known, the row is demultiplicated
protospace_df["Gene"] = protospace_df["Gene"].apply(lambda x: x.split("/") if isinstance(x, str) else x)
protospace_df = protospace_df.explode("Gene").reset_index(drop=True)

adamson_perturb = adamson_perturb[(
    # retrieve guide identity in ther protospace table
    (pert := adamson_perturb.obs["guide identity"]).isin(
        (protospace_df["Gene"].dropna() + "_" + protospace_df["Perturb-seq_Vector_ID"]).dropna()) |
    # retrieve control with large occurence (more than 100 cells)
    (pert.str.contains("mod") & pert.isin(pert.value_counts()[pert.value_counts() > 100].index))
)]

/tmp/ipykernel_1054917/2867053296.py:3: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  ~adamson_pilot.obs["guide identity"].astype(str).str.contains(r"(nan|\*)")
/tmp/ipykernel_1054917/2867053296.py:7: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  adamson_epistasis.obs["guide identity"].astype(str).str.contains("(ctrl|IRE1|PERK|ATF6)")
/home/hhakem/projects/cellarium-ml/.venv/lib/python3.11/site-packages/openpyxl/worksheet/_reader.py:329: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


#### ii) Formatting Adamson

Add more metadata:
- `gene_name`
- parse `guide identity`:
  - `target`
    - **Renaming target:**
      - GSM2406675_10X001
        - Control is written with 'mod'. Should be renamed in 'control'
      - GSM2406677_10X005
        - IRE1 -> ERN1 to match the actual gene name
        - PERK -> EIF2AK3 to match the actual gene name
        - Single perturbation should have the 'only' removed
        - Double or Triple perturbations should be spaced with '+'
        - Controls are written with 'ctrl'. Should be renamed in 'control'
      - GSM2406681_10X010
        - Controls are written with 'ctrl'. Should be renamed in 'control'
  - `plasmid`
- original `cell_barcode`
- add `cell_type` (using the paper)
  individually transduced chronic myeloid leukemia cells (K562)
  
    | **Experimental Models: Cell Lines** | 
    | - |
    | cBA010 (K562 UPRE reporter cell line, parental) |
    | cBA011 (cBA010 stably transduced with pBA409) |
    | GFP+ K562 dCas9-KRAB cell line  |
    | cMJ006 (GFP+ K562 dCas9-KRAB cell line stably transduced with pMH0001) |


**Retrieve gene name**

In [ ]:
%%bash
cd ../../ # cd to root of the project
python fine_tune/scripts/genome.py

In [ ]:
gene_name = pd.read_csv(
    data_path.joinpath("genome/gencode.v32.primary_assembly.annotation.csv"),
    index_col="ensemble_id"
)

#### Parse target and plasmid from guide identity

In [ ]:
map_guide_id = {
    g: {"target": "_".join(g_split[:-1]),
        "plasmid":  g_split[-1]}
        for g in adata_adamson.obs["guide identity"].unique().astype(str)
        if (_g_split := g.split("_")) and
           (g_split := _g_split if len(_g_split) > 1 else _g_split * 2)
}

In [ ]:
adata_adamson.obs = adata_adamson.obs.join(
    adata_adamson.obs["guide identity"].astype(str).to_frame().join(
        pd.DataFrame(map_guide_id).T,
        on="guide identity"
    ).drop(columns=["guide identity"])
)

#### Get original barcode

In [ ]:
adata_adamson.obs["cell_barcode"] = adata_adamson.obs_names.to_series().str.split("_").apply(lambda split: split[0])

### c) Why not to use Gears Adamson

In [246]:
gears_adamson = ad.read_h5ad(next((data_path / "anndata/gears_adamson").glob("*.h5ad")))
print(gears_adamson,"\n")
print(gears_adamson.obs.to_string())

AnnData object with n_obs × n_vars = 68603 × 5060
    obs: 'condition', 'cell_type', 'dose_val', 'control', 'condition_name'
    var: 'gene_name'
    uns: 'non_dropout_gene_idx', 'non_zeros_gene_idx', 'rank_genes_groups_cov_all', 'top_non_dropout_de_20', 'top_non_zero_de_20' 

                        condition cell_type dose_val  control             condition_name
cell_barcode                                                                            
AAACATACACCGAT-1       CREB1+ctrl   K562(?)      1+1        0     K562(?)_CREB1+ctrl_1+1
AAACATACAGAGAT-1             ctrl   K562(?)        1        1             K562(?)_ctrl_1
AAACATACCAGAAA-1             ctrl   K562(?)        1        1             K562(?)_ctrl_1
AAACATACGTTGAC-1             ctrl   K562(?)        1        1             K562(?)_ctrl_1
AAACATACTGTTCT-1             ctrl   K562(?)        1        1             K562(?)_ctrl_1
AAACCGTGCAGCTA-1      ZNF326+ctrl   K562(?)      1+1        0    K562(?)_ZNF326+ctrl_1+1
AAACCGTGCC

#### Get condition from gears

In [252]:
adata_adamson_not_gears = adata_adamson[(~adata_adamson.obs["cell_barcode"].isin(gears_adamson.obs_names))].copy()
adata_adamson_gears = adata_adamson[(adata_adamson.obs["cell_barcode"].isin(gears_adamson.obs_names))].copy()
adata_adamson_gears.obs = adata_adamson_gears.obs.join(
    gears_adamson.obs["condition"].str.split("+").apply(lambda cond: cond[0]),
    on="cell_barcode"
).rename(columns={"condition": "gears_condition"})

In [253]:
gears_adamson.obs

condition cell_type dose_val  control  \
cell_barcode                                                   
AAACATACACCGAT-1      CREB1+ctrl   K562(?)      1+1        0   
AAACATACAGAGAT-1            ctrl   K562(?)        1        1   
AAACATACCAGAAA-1            ctrl   K562(?)        1        1   
AAACATACGTTGAC-1            ctrl   K562(?)        1        1   
AAACATACTGTTCT-1            ctrl   K562(?)        1        1   
...                          ...       ...      ...      ...   
TTTGCATGCTTTAC-10     STT3A+ctrl   K562(?)      1+1        0   
TTTGCATGGAGGAC-10  ARHGAP22+ctrl   K562(?)      1+1        0   
TTTGCATGTAGAGA-10           ctrl   K562(?)        1        1   
TTTGCATGTCAAGC-10    KCTD16+ctrl   K562(?)      1+1        0   
TTTGCATGTGGAGG-10    SAMM50+ctrl   K562(?)      1+1        0   

                              condition_name  
cell_barcode                                  
AAACATACACCGAT-1      K562(?)_CREB1+ctrl_1+1  
AAACATACAGAGAT-1              K562(?)_ctrl_1  
AAACATACCAGAAA-1              K562(?)_ctrl_1  
AAACATACGTTGAC-1              K562(?)_ctrl_1  
AAACATACTGTTCT-1              K562(?)_ctrl_1  
...                                      ...  
TTTGCATGCTTTAC-10     K562(?)_STT3A+ctrl_1+1  
TTTGCATGGAGGAC-10  K562(?)_ARHGAP22+ctrl_1+1  
TTTGCATGTAGAGA-10             K562(?)_ctrl_1  
TTTGCATGTCAAGC-10    K562(?)_KCTD16+ctrl_1+1  
TTTGCATGTGGAGG-10    K562(?)_SAMM50+ctrl_1+1  

[68603 rows x 5 columns]

In [254]:
mismatch = (
    adata_adamson_gears[
        adata_adamson_gears.obs["target"] != adata_adamson_gears.obs["gears_condition"]
    ].obs[["target", "gears_condition"]]
    .groupby(["target", "gears_condition"])
    .size().unstack(fill_value=0)
)
mismatch["ctrl"][mismatch["ctrl"] > 100]


target
3x_neg_ctrl       3124
62(mod)           1655
63(mod)           4599
ASCC3              959
ATF6_IRE1         1326
ATF6_PERK         1456
ATF6_PERK_IRE1    1542
ATF6_only         1549
DNAJC19            831
EP300              561
IRE1_only         1550
PERK_IRE1         1511
PERK_only         1422
SEC61B            1003
SNAI1              527
SPI1               645
Name: ctrl, dtype: int64

In [255]:
# adata_adamson[~adata_adamson.obs["experiment"].isin(["GSM2406681_10X010"])].obs["target"].unique()
count_vs_mismatch = adata_adamson_gears.obs["target"].value_counts().to_frame().join(
    pd.Series(mismatch.sum(axis=1), name="mismatch")).dropna()
count_vs_mismatch["percentage"] = (100 * count_vs_mismatch["mismatch"] / count_vs_mismatch["count"]).round(1)
adata_adamson_gears.obs = adata_adamson_gears.obs.join(
    count_vs_mismatch,
    on="target"
)

In [256]:
adata_adamson_gears.obs = adata_adamson_gears.obs.join(
    pd.Series(adata_adamson_gears.obs["experiment"].value_counts(), name="tot_count_by_experiment"),
    on="experiment"
)

In [257]:
adata_adamson_gears.obs = adata_adamson_gears.obs.join(
    (adata_adamson_gears.obs[["mismatch", "experiment"]].drop_duplicates()
     .groupby(["experiment"]).sum()
     .rename(columns={"mismatch": "tot_mismatch"})),
    on="experiment"
)

In [258]:
adata_adamson_gears.obs["percentage_tot_mismatch_by_experiment"] = (
    100 * adata_adamson_gears.obs["tot_mismatch"] / adata_adamson_gears.obs["tot_count_by_experiment"]
).round(1)

In [259]:
gears_adamson

AnnData object with n_obs × n_vars = 68603 × 5060
    obs: 'condition', 'cell_type', 'dose_val', 'control', 'condition_name'
    var: 'gene_name'
    uns: 'non_dropout_gene_idx', 'non_zeros_gene_idx', 'rank_genes_groups_cov_all', 'top_non_dropout_de_20', 'top_non_zero_de_20'

In [260]:
adata_adamson_gears

AnnData object with n_obs × n_vars = 68663 × 35635
    obs: 'guide identity', 'read count', 'UMI count', 'coverage', 'good coverage', 'number of cells', 'experiment', 'target', 'plasmid', 'cell_barcode', 'gears_condition', 'count', 'mismatch', 'percentage', 'tot_count_by_experiment', 'tot_mismatch', 'percentage_tot_mismatch_by_experiment'
    var: 'gene_name'

In [261]:
adata_adamson_gears.obs[["percentage_tot_mismatch_by_experiment", "experiment"]].drop_duplicates()

percentage_tot_mismatch_by_experiment  \
AAACATACACCGAT-1_GSM2406675_10X001                                   63.7   
AAACATACACTCAG-1_GSM2406677_10X005                                  100.0   
AAACATACAAGATG-1_GSM2406681_10X010                                   14.9   

                                           experiment  
AAACATACACCGAT-1_GSM2406675_10X001  GSM2406675_10X001  
AAACATACACTCAG-1_GSM2406677_10X005  GSM2406677_10X005  
AAACATACAAGATG-1_GSM2406681_10X010  GSM2406681_10X010

In [262]:
adata_adamson_gears.obs[adata_adamson_gears.obs["percentage"] > 5].groupby(["experiment", "target"]).size().unstack(fill_value=0)

target             *  3x_neg_ctrl  62(mod)  63(mod)  ASCC3  ATF6_IRE1  \
experiment                                                              
GSM2406675_10X001  0            0     1655        0      0          0   
GSM2406677_10X005  0         3127        0        0      0       1328   
GSM2406681_10X010  1            0        0     4600   1482          0   

target             ATF6_PERK  ATF6_PERK_IRE1  ATF6_only  DNAJC19  EP300  \
experiment                                                                
GSM2406675_10X001          0               0          0        0    561   
GSM2406677_10X005       1459            1546       1553        0      0   
GSM2406681_10X010          0               0          0     1276      0   

target             Gal4-4(mod)  IRE1_only  PERK_IRE1  PERK_only  SEC61B  \
experiment                                                                
GSM2406675_10X001            0          0          0          0       0   
GSM2406677_10X005            0       1552       1516       1425       0   
GSM2406681_10X010            7          0          0          0    1429   

target             SNAI1  SPI1  nan  
experiment                           
GSM2406675_10X001    527   646    0  
GSM2406677_10X005      0     0    3  
GSM2406681_10X010      0     0    0

### Raw Norman

In [ ]:
# Define paths
norman_dir = data_path.joinpath("raw/raw_norman")

# Load gene and barcode names
genes = pd.read_csv(norman_dir / "genes.tsv.gz", header=None, sep="\t")
barcodes = pd.read_csv(norman_dir / "barcodes.tsv.gz", header=None)

# Load cell identities
cell_identities = pd.read_csv(norman_dir / "cell_identities.csv.gz", index_col=0)

# Build AnnData
adata_norman = ad.io.read_mtx(norman_dir / "matrix.mtx.gz").T
adata_norman.var_names = genes[0].values
adata_norman.obs_names = barcodes[0].values
# adata.obs = cell_identities.loc[adata.obs_names] fail because more barcodes than cell_identity.
adata_norman.obs = pd.DataFrame(index=adata_norman.obs_names)
adata_norman.obs = adata_norman.obs.join(cell_identities) # fill with NaN barcodes with non found identity

## Filtering

**Quality Control:**

- Mitochondrial genes
- Ribosomal genes
- hemoglobin genes

**Doublet Detection:**